In [4]:
import src.data.breathe_data as br
import plotly.express as px
import src.modelling_fef2575.hfef2575 as hfef2575

In [2]:
# df = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_inferred_AR_IA").drop(columns=["AR", "IA"])
# df = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_inferred_AR_IA").drop(columns=["AR", "IA"])
# df = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_Nan_processed")
df = br.load_meas_from_excel("BR_O2_FEV1_FEF2575_PEF_inferred_AR_IA_processed").drop(columns=["AR", "IA"])

In [3]:
df.head()

ID Date Recorded  FEV1  O2 Saturation  FEF2575  PEF  ecFEV1  Age   Sex  \
0  101    2021-05-25  1.68             98     1.17  227    1.69   53  Male   
1  101    2021-05-26  1.65             98     1.06  236    1.69   53  Male   
2  101    2021-05-27  1.69             98     1.12  183    1.69   53  Male   
3  101    2021-05-28  1.67             98     1.08  175    1.69   53  Male   
4  101    2021-05-29  1.69             98     1.16  171    1.76   53  Male   

   Height  ...  ecFEV1 % Predicted  FEV1 % Predicted  O2 Saturation % Healthy  \
0   173.0  ...           46.813611         46.536607               100.874827   
1   173.0  ...           46.813611         45.705597               100.874827   
2   173.0  ...           46.813611         46.813611               100.874827   
3   173.0  ...           46.813611         46.259604               100.874827   
4   173.0  ...           48.752636         46.813611               100.874827   

   PEF (L/s)  FEF2575%PEF    AR mean   IA mean  ecFEV1_2  ecFEF2575_2  \
0   3.783333    30.925110  47.601368  0.654616      1.69         1.17   
1   3.933333    26.949153  47.601368  0.654616      1.69         1.17   
2   3.050000    36.721311  47.601368  0.654616      1.69         1.12   
3   2.916667    37.028571  47.601368  0.654616      1.69         1.16   
4   2.850000    40.701754  44.593062  0.667227      1.76         1.16   

   ecPEF (L/s)_2  
0       3.933333  
1       3.933333  
2       3.933333  
3       3.050000  
4       3.116667  

[5 rows x 22 columns]

In [10]:
def calc_predicted_FEF2575_LMS_df(df):
    """
    Returns a Series with Predicted FEV1 from a DataFrame with Sex, Height, Age
    """
    df["Predicted FEF2575"] = df.apply(
        lambda x: hfef2575.calc_predicted_FEV1_LMS(
            hfef2575.load_LMS_spline_vals(x.Age, x.Sex),
            hfef2575.load_LMS_coeffs(x.Sex),
            x.Height,
            x.Age,
            x.Sex,
        )["M"],
        axis=1,
    )
    # df.apply(lambda x: sanity_checks.predicted_fev1(x["Predicted FEV1"], x.ID), axis=1)
    return df

def calc_FEVF2575_prct_predicted_df(df):
    """
    Returns input DataFrame with FEV1 % Predicted as a new column, after sanity check
    """
    df["ecFEF2575 % Predicted"] = df["ecFEF2575_2"] / df["Predicted FEF2575"] * 100
    # df.apply(
    #     lambda x: sanity_checks.fev1_prct_predicted(x["ecFEV1 % Predicted"], x.ID),
    #     axis=1,
    # )
    # df["FEV1 % Predicted"] = df["FEV1"] / df["Predicted FEV1"] * 100
    # df.apply(
    #     lambda x: sanity_checks.fev1_prct_predicted(x["FEV1 % Predicted"], x.ID), axis=1
    # )
    return df

In [11]:
# Add Healthy FEF2575
# df["Heatlhy FEF2575"] = 
df = calc_predicted_FEF2575_LMS_df(df)
df = calc_FEVF2575_prct_predicted_df(df)

## PEF, FEF2575 data quality

In [4]:
# Using plotly create histogram of fef2575%pef
fig = px.histogram(df, x="PEF", nbins=500)
fig.show()

In [18]:
df[df.PEF < 80]

ID Date Recorded  FEV1  O2 Saturation  FEF2575  PEF  ecFEV1  Age  \
1543   111    2022-05-14  0.70             80     0.37   72    1.45   37   
1547   111    2022-05-19  0.88             85     0.40   78    0.93   37   
1548   111    2022-05-20  0.90             80     0.50   76    0.90   37   
1549   111    2022-05-21  0.78             86     0.46   77    0.90   37   
1551   111    2022-05-23  0.84             82     0.47   76    0.85   37   
1552   111    2022-05-25  0.76             83     0.39   71    0.97   37   
5965   198    2021-06-13  0.59             96     0.41   62    1.07   36   
6005   198    2021-07-27  0.63             96     0.38   70    0.98   36   
10300  242    2022-06-20  2.66             99     2.52   73    2.66   39   
10409  248    2022-06-02  0.66             98     0.45   75    0.95   44   
10414  248    2022-06-09  0.69             99     0.43   79    0.99   44   
10419  248    2022-06-22  0.73             98     0.45   76    1.10   44   
10425  248    2022-07-21  0.74             99     0.41   78    1.16   44   
12145  272    2022-09-05  1.57             94     0.74   77    1.81   57   

          Sex  Height  Predicted FEV1  Healthy O2 Saturation  \
1543   Female   167.0        3.267960              98.078678   
1547   Female   167.0        3.267960              98.078678   
1548   Female   167.0        3.267960              98.078678   
1549   Female   167.0        3.267960              98.078678   
1551   Female   167.0        3.267960              98.078678   
1552   Female   167.0        3.267960              98.078678   
5965   Female   151.0        2.657664              98.365670   
6005   Female   151.0        2.657664              98.365670   
10300  Female   165.0        3.138644              98.114552   
10409  Female   154.0        2.601447              98.311859   
10414  Female   154.0        2.601447              98.311859   
10419  Female   154.0        2.601447              98.311859   
10425  Female   154.0        2.601447              98.311859   
12145  Female   165.0        2.663838              98.114552   

       ecFEV1 % Predicted  FEV1 % Predicted  O2 Saturation % Healthy  \
1543            44.370185         21.420090                81.567168   
1547            28.458119         26.928113                86.665116   
1548            27.540115         27.540115                81.567168   
1549            27.540115         23.868100                87.684705   
1551            26.010109         25.704107                83.606347   
1552            29.682124         23.256097                84.625937   
5965            40.260925         22.199950                97.595025   
6005            36.874492         23.705031                97.595025   
10300           84.749978         84.749978               100.902463   
10409           36.518143         25.370499                99.682786   
10414           38.055749         26.523704               100.699957   
10419           42.284165         28.061310                99.682786   
10425           44.590574         28.445711               100.699957   
12145           67.947074         58.937518                95.806379   

       PEF (L/s)  FEF2575%PEF    AR mean    IA mean  
1543    1.200000    30.833333  53.276862  17.679347  
1547    1.300000    30.769231  70.713326  11.232568  
1548    1.266667    39.473684  70.713326  16.460029  
1549    1.283333    35.844156  70.713326  10.189394  
1551    1.266667    37.105263  72.298543  14.117860  
1552    1.183333    32.957746  69.127958  13.540670  
5965    1.033333    39.677419  57.845028   1.600953  
6005    1.166667    32.571429  61.571207   1.470408  
10300   1.216667   207.123288  15.247999   0.739259  
10409   1.250000    36.000000  59.052326   0.755174  
10414   1.316667    32.658228  57.983442   0.623116  
10419   1.266667    35.526316  53.529309   0.805991  
10425   1.300000    31.538462  50.369662   0.659730  
12145   1.283333    57.662338  28.969152   4.082679

In [4]:
# Using plotly create histogram of fef2575%pef
fig = px.histogram(df, x="FEF2575%PEF")
fig.show()

In [17]:
# Why are there measurements > 100? even > 70?

# If the test is well performed, FEF2575 should never be > than PEF
# Or the PEF is super low
print(len(df[df["FEF2575%PEF"] > 70]) / len(df) * 100, "% are > 70%")

df[df["FEF2575%PEF"] > 100]

0.10411244143675169 % are > 70%


ID Date Recorded  FEV1  O2 Saturation  FEF2575  PEF  ecFEV1  Age  \
8234   220    2023-05-05  1.74            100     6.92  406    1.79   41   
10145  242    2021-06-28  3.17             98     3.87  213    3.17   39   
10300  242    2022-06-20  2.66             99     2.52   73    2.66   39   
10688  250    2022-07-21  4.57             98     5.28  260    4.57   37   
10781  250    2023-03-08  4.21             97     4.75  201    4.26   37   

          Sex  Height  Predicted FEV1  Healthy O2 Saturation  \
8234   Female   166.0        3.128822              98.096615   
10145  Female   165.0        3.138644              98.114552   
10300  Female   165.0        3.138644              98.114552   
10688    Male   169.0        3.849069              97.221852   
10781    Male   169.0        3.849069              97.221852   

       ecFEV1 % Predicted  FEV1 % Predicted  O2 Saturation % Healthy  \
8234            57.210025         55.611979               101.940317   
10145          100.999034        100.999034                99.883247   
10300           84.749978         84.749978               100.902463   
10688          118.730020        118.730020               100.800384   
10781          110.676124        109.377109                99.771808   

       PEF (L/s)  FEF2575%PEF    AR mean   IA mean  
8234    6.766667   102.266010  36.675736  0.595679  
10145   3.550000   109.014085   7.592125  0.994936  
10300   1.216667   207.123288  15.247999  0.739259  
10688   4.333333   121.846154   3.910145  0.753682  
10781   3.350000   141.791045   5.160572  1.032076

In [13]:
# PEF should be greater than FEV1
idx = df[df["PEF (L/s)"] < df["FEV1"]].index
df[df["PEF (L/s)"] < df["FEV1"]]

ID Date Recorded  FEV1  O2 Saturation  FEF2575  PEF  ecFEV1  Age  \
10300  242    2022-06-20  2.66             99     2.52   73    2.66   39   
10688  250    2022-07-21  4.57             98     5.28  260    4.57   37   
10781  250    2023-03-08  4.21             97     4.75  201    4.26   37   
12145  272    2022-09-05  1.57             94     0.74   77    1.81   57   

          Sex  Height  ...  O2 Saturation % Healthy  PEF (L/s)  FEF2575%PEF  \
10300  Female   165.0  ...               100.902463   1.216667   207.123288   
10688    Male   169.0  ...               100.800384   4.333333   121.846154   
10781    Male   169.0  ...                99.771808   3.350000   141.791045   
12145  Female   165.0  ...                95.806379   1.283333    57.662338   

         AR mean   IA mean  ecFEV1_2  ecFEF2575_2  ecPEF (L/s)_2  \
10300  15.247999  0.739259      2.66         2.52       7.700000   
10688   3.910145  0.753682      4.57         5.28      11.450000   
10781   5.160572  1.032076      4.26         5.25      11.950000   
12145  28.969152  4.082679      1.81         0.96       6.333333   

       Predicted FEF2575  ecFEF2575 % Predicted  
10300           3.290428              76.585773  
10688           3.897389             135.475330  
10781           3.897389             134.705584  
12145           2.457357              39.066364  

[4 rows x 24 columns]

In [14]:
df1 = df.drop(idx, axis=0, inplace=False)

In [20]:
# FEF2575 should be lower than FEV1, otherwise:
# Test not well performed: PEF reached late -> flow increase over a long time (0.5s-0.1s) instead of 0.1s, little dynamic compression of the airways
df[df.FEV1 < df.FEF2575].sort_values(by="FEV1")

ID Date Recorded  FEV1  O2 Saturation  FEF2575  PEF  ecFEV1  Age  \
10428  248    2022-10-11  0.78             98     0.93  170    1.06   44   
10429  248    2023-08-01  1.06             98     1.07  201    1.06   44   
6975   202    2021-10-29  1.23             82     1.99  217    1.85   64   
9263   238    2022-12-28  1.25             98     2.99  300    1.28   59   
932    102    2023-10-18  1.39             96     1.52  351    1.39   45   
...    ...           ...   ...            ...      ...  ...     ...  ...   
1686   113    2021-07-26  5.10             98     5.12  502    5.27   26   
1692   113    2021-09-06  5.12             98     5.14  393    5.12   26   
1678   113    2021-06-16  5.13             98     5.36  508    5.13   26   
1701   113    2021-12-13  5.25             98     5.33  585    5.25   26   
1687   113    2021-08-02  5.27             99     5.30  493    5.27   26   

          Sex  Height  Predicted FEV1  Healthy O2 Saturation  \
10428  Female   154.0        2.601447              98.311859   
10429  Female   154.0        2.601447              98.311859   
6975   Female   157.0        2.213968              98.258048   
9263   Female   165.0        2.606672              98.114552   
932      Male   176.0        3.987357              97.096293   
...       ...     ...             ...                    ...   
1686     Male   165.5        3.923640              97.284632   
1692     Male   165.5        3.923640              97.284632   
1678     Male   165.5        3.923640              97.284632   
1701     Male   165.5        3.923640              97.284632   
1687     Male   165.5        3.923640              97.284632   

       ecFEV1 % Predicted  FEV1 % Predicted  O2 Saturation % Healthy  \
10428           40.746559         29.983317                99.682786   
10429           40.746559         40.746559                99.682786   
6975            83.560392         55.556369                83.453724   
9263            49.104751         47.953858                99.883247   
932             34.860181         34.860181                98.870921   
...                   ...               ...                      ...   
1686           134.314070        129.981358               100.735335   
1692           130.491089        130.491089               100.735335   
1678           130.745954        130.745954               100.735335   
1701           133.804339        133.804339               100.735335   
1687           134.314070        134.314070               101.763247   

       PEF (L/s)  FEF2575%PEF    AR mean    IA mean  
10428   2.833333    32.823529  55.443476   0.789030  
10429   3.350000    31.940299  55.443476   0.789030  
6975    3.616667    55.023041  16.609544  16.533523  
9263    5.000000    59.800000  45.968913   0.828017  
932     5.850000    25.982906  62.398152   0.905130  
...          ...          ...        ...        ...  
1686    8.366667    61.195219   2.315685   0.766121  
1692    6.550000    78.473282   2.569853   0.766121  
1678    8.466667    63.307087   2.569853   0.766121  
1701    9.750000    54.666667   2.315685   0.766121  
1687    8.216667    64.503043   2.315685   0.622701  

[3111 rows x 19 columns]

# Modelling FEF2575

In [8]:
# fig = px.scatter(df1, x="FEV1", y="FEF2575", color="ID")
fig = px.scatter(df1, x="ecFEV1_2", y="ecFEF2575_2", color="ID")
fig.update_traces(marker=dict(size=3))
fig.update_layout(width=800, height=800)
fig.show()

In [13]:
fig = px.scatter(df1, x="ecPEF (L/s)_2", y="ecFEF2575_2", color="ID")
# fig = px.scatter(df1, x="PEF (L/s)", y="FEF2575", color="ID")
fig.update_traces(marker=dict(size=3))
# Update the layout to show othonormal axises
fig.update_layout(width=1200, height=600)
fig.show()

In [12]:
df1

ID Date Recorded  FEV1  O2 Saturation  FEF2575  PEF  ecFEV1  Age  \
0      101    2021-05-25  1.68             98     1.17  227    1.69   53   
1      101    2021-05-26  1.65             98     1.06  236    1.69   53   
2      101    2021-05-27  1.69             98     1.12  183    1.69   53   
3      101    2021-05-28  1.67             98     1.08  175    1.69   53   
4      101    2021-05-29  1.69             98     1.16  171    1.76   53   
...    ...           ...   ...            ...      ...  ...     ...  ...   
15363  357    2021-07-06  2.67             98     2.64  398    2.67   24   
15364  358    2021-05-28  4.36             98     4.39  445    4.36   18   
15365  358    2021-05-29  4.21             96     3.90  467    4.36   18   
15366  358    2021-05-30  4.26             98     3.89  457    4.34   18   
15367  358    2021-05-31  4.34             98     4.24  521    4.34   18   

          Sex  Height  ...  FEV1 % Predicted  O2 Saturation % Healthy  \
0        Male   173.0  ...         46.536607               100.874827   
1        Male   173.0  ...         45.705597               100.874827   
2        Male   173.0  ...         46.813611               100.874827   
3        Male   173.0  ...         46.259604               100.874827   
4        Male   173.0  ...         46.813611               100.874827   
...       ...     ...  ...               ...                      ...   
15363  Female   164.0  ...         79.515803                99.864990   
15364    Male   177.0  ...         96.774005               100.949381   
15365    Male   177.0  ...         93.444624                98.889190   
15366    Male   177.0  ...         94.554418               100.949381   
15367    Male   177.0  ...         96.330087               100.949381   

       PEF (L/s)  FEF2575%PEF    AR mean   IA mean  ecFEV1_2  ecFEF2575_2  \
0       3.783333    30.925110  47.601368  0.654616      1.69         1.17   
1       3.933333    26.949153  47.601368  0.654616      1.69         1.17   
2       3.050000    36.721311  47.601368  0.654616      1.69         1.12   
3       2.916667    37.028571  47.601368  0.654616      1.69         1.16   
4       2.850000    40.701754  44.593062  0.667227      1.76         1.16   
...          ...          ...        ...       ...       ...          ...   
15363   6.633333    39.798995  19.247868  1.000480      2.67         2.74   
15364   7.416667    59.191011   8.712451  0.727311      4.36         4.39   
15365   7.783333    50.107066   8.712451  1.456096      4.36         4.39   
15366   7.616667    51.072210   9.167144  0.727311      4.34         4.24   
15367   8.683333    48.829175   9.167144  0.727311      4.34         4.24   

       ecPEF (L/s)_2  FEF2575%FEV1  
0           3.933333     69.642857  
1           3.933333     64.242424  
2           3.933333     66.272189  
3           3.050000     64.670659  
4           3.116667     68.639053  
...              ...           ...  
15363       6.633333     98.876404  
15364       7.783333    100.688073  
15365       7.783333     92.636580  
15366       8.683333     91.314554  
15367       8.683333     97.695853  

[15364 rows x 23 columns]

In [20]:
df1["FEF2575%FEV1"] = df1["FEF2575"] / df1["FEV1"] * 100
df1["FEF2575%FEV1_2"] = df1["ecFEF2575_2"] / df1["ecFEV1_2"] * 100
df1["FEF2575%PEF"] = df1["FEF2575"] / df1["PEF (L/s)"] * 100
df1["FEF2575%PEF_2"] = df1["ecFEF2575_2"] / df1["ecPEF (L/s)_2"] * 100

In [21]:
fig = px.scatter(df1, x="AR mean", y="FEF2575%FEV1_2", color="ID")
fig.update_traces(marker=dict(size=2))
fig.update_layout(width=1200, height=800)
# Update y axis ranve
fig.update_yaxes(range=[0, 250])
fig.show()

In [23]:
fig = px.scatter(df1, x="AR mean", y="FEF2575%PEF_2", color="ID")
fig.update_traces(marker=dict(size=2))
fig.update_layout(width=1200, height=800)
fig.show()

In [16]:
fig = px.scatter(df1, x="AR mean", y="ecFEF2575 % Predicted", color="ID")
fig.update_traces(marker=dict(size=2))
fig.update_layout(width=1200, height=800)
fig.show()

In [17]:
fig = px.scatter(df1, x="IA mean", y="FEF2575%PEF", color="ID")
fig.update_traces(marker=dict(size=2))
fig.update_layout(width=1200, height=800)
fig.show()

In [44]:
fig = px.scatter(df1, x="IA mean", y="FEV1", color="ID")
fig.update_traces(marker=dict(size=2))
fig.update_layout(width=1200, height=800)
fig.show()